### Registering entities represented in grocery dataset

In FeatureByte, an "entity" models real-world objects and ideas. These entities often correspond to columns in database tables.

Taking our grocery scenario as an example, we can view "Customer", "Invoice", and "Item" as entities.

To help FeatureByte identify these entities in the data and the columns that represent them, we'll be creating and tagging these entities in this tutorial.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:39:07 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:39:07 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:39:07 | INFO     | SDK version: 0.6.0.dev121
16:39:07 | INFO     | No catalog activated.
16:39:07 | INFO     | 10 feature lists, 59 features deployed
16:39:07 | INFO     | Using profile: tutorial
16:39:07 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:39:07 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:39:08 | INFO     | SDK version: 0.6.0.dev121
16:39:08 | INFO     | No catalog activated.
16:39:08 | INFO     | 10 feature lists, 59 features deployed
16:39:08 | INFO     | Catalog activated: Grocery Dataset Tutorial


As previously discussed, we'll establish the following entities:
- customer - an individual shopping at the stores
- invoice - a record of the customer's purchase
- item - individual items on the invoice
- product - products available in the store for purchase
- productgroup - the category or group a product falls under
- frenchstate - a region in France (since our dataset revolves around French grocery stores and their customers)

It's worth noting that the count of entities doesn't necessarily have to align with the number of tables. An entity is a business-oriented term, and multiple entities might be represented within a single table.

When creating an entity, you'll need to define its [serving name](https://docs.featurebyte.com/0.5/about/glossary/#entity-serving-name). This name acts as a unique identifier, particularly during preview or serving requests.

In [2]:
catalog.create_entity(name="customer", serving_names=["GROCERYCUSTOMERGUID"])
catalog.create_entity(name="invoice", serving_names=["GROCERYINVOICEGUID"])
catalog.create_entity(name="item", serving_names=["GROCERYINVOICEITEMGUID"])
catalog.create_entity(name="product", serving_names=["GROCERYPRODUCTGUID"])
catalog.create_entity(name="productgroup", serving_names=["PRODUCTGROUP"])
catalog.create_entity(name="frenchstate", serving_names=["FRENCHSTATE"])

<featurebyte.api.entity.Entity at 0x14a96ee80>
{
  'name': 'frenchstate',
  'created_at': '2023-11-27T15:39:12.830000',
  'updated_at': None,
  'description': None,
  'serving_names': [
    'FRENCHSTATE'
  ],
  'catalog_name': 'Grocery Dataset Tutorial'
}

Now that we've established the entities, it's time to guide FeatureByte in mapping these entities to the actual data in our tables.

In [3]:
customer_table = catalog.get_table("GROCERYCUSTOMER")
invoice_table = catalog.get_table("GROCERYINVOICE")
items_table = catalog.get_table("INVOICEITEMS")
product_table = catalog.get_table("GROCERYPRODUCT")

In [4]:
# tag the entities for the grocery customer table
customer_table.GroceryCustomerGuid.as_entity("customer")
customer_table.State.as_entity("frenchstate")

# tag the entities for the grocery invoice table
invoice_table.GroceryInvoiceGuid.as_entity("invoice")
invoice_table.GroceryCustomerGuid.as_entity("customer")

# tag the entities for the grocery items table
items_table.GroceryInvoiceItemGuid.as_entity("item")
items_table.GroceryInvoiceGuid.as_entity("invoice")
items_table.GroceryProductGuid.as_entity("product")

# tag the entities for the grocery product table
product_table.GroceryProductGuid.as_entity("product")
product_table.ProductGroup.as_entity("productgroup")

Now, if we list the tables as we did in the previous tutorial, we'll notice that entities have been assigned to each table.

In [5]:
display(catalog.list_tables())

id             name             type        status  \
0  6564b7edbeba6c193e0fe3be   GROCERYPRODUCT  dimension_table  PUBLIC_DRAFT   
1  6564b7ecbeba6c193e0fe3bd     INVOICEITEMS       item_table  PUBLIC_DRAFT   
2  6564b7ebbeba6c193e0fe3bc   GROCERYINVOICE      event_table  PUBLIC_DRAFT   
3  6564b7eabeba6c193e0fe3bb  GROCERYCUSTOMER        scd_table  PUBLIC_DRAFT   

                   entities                  created_at  
0   [product, productgroup]  2023-11-27T15:38:22.276000  
1  [item, invoice, product]  2023-11-27T15:38:21.489000  
2       [invoice, customer]  2023-11-27T15:38:20.150000  
3   [customer, frenchstate]  2023-11-27T15:38:19.300000

We can also list entities separately: 

In [6]:
display(catalog.list_entities())

id          name             serving_names  \
0  6564b820d5b79db93bea9f62   frenchstate             [FRENCHSTATE]   
1  6564b81fd5b79db93bea9f61  productgroup            [PRODUCTGROUP]   
2  6564b81ed5b79db93bea9f60       product      [GROCERYPRODUCTGUID]   
3  6564b81ed5b79db93bea9f5f          item  [GROCERYINVOICEITEMGUID]   
4  6564b81dd5b79db93bea9f5e       invoice      [GROCERYINVOICEGUID]   
5  6564b81cd5b79db93bea9f5d      customer     [GROCERYCUSTOMERGUID]   

                   created_at  
0  2023-11-27T15:39:12.830000  
1  2023-11-27T15:39:12.144000  
2  2023-11-27T15:39:11.513000  
3  2023-11-27T15:39:10.832000  
4  2023-11-27T15:39:10.155000  
5  2023-11-27T15:39:09.477000

And let's examine the relationships between entities, which FeatureByte has conveniently outlined for us:

In [7]:
display(catalog.list_relationships())

id relationship_type    entity related_entity  \
0  6564b82baee16c542a9c584e      child_parent   product   productgroup   
1  6564b82aaee16c542a9c5848      child_parent      item        product   
2  6564b8296f39a417e1370da7      child_parent      item        invoice   
3  6564b82735af4043fe90845e      child_parent   invoice       customer   
4  6564b82635af4043fe908457      child_parent  customer    frenchstate   

    relation_table relation_table_type  enabled                  created_at  \
0   GROCERYPRODUCT     dimension_table     True  2023-11-27T15:39:23.509000   
1     INVOICEITEMS          item_table     True  2023-11-27T15:39:22.162000   
2     INVOICEITEMS          item_table     True  2023-11-27T15:39:21.588000   
3   GROCERYINVOICE         event_table     True  2023-11-27T15:39:19.998000   
4  GROCERYCUSTOMER           scd_table     True  2023-11-27T15:39:18.646000   

  updated_at  
0       None  
1       None  
2       None  
3       None  
4       None

That's it for most important data modeling concepts in FeatureByte. 
In next tutorials we will look into concepts related to data cleaning and feature engineering. 

### For more details about concepts we discussed in this tutorial, feel free to explore:
- [More info on Entities](https://docs.featurebyte.com/latest/about/glossary/#entities-and-relationships)

#### SDK reference for
- [Entity](https://docs.featurebyte.com/latest/reference/core/entity/)
- [Catalog.create_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.catalog.Catalog.create_entity/)
- [TableColumn.as_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.base_table.TableColumn.as_entity/)